In [2]:
import pandas as pd
import numpy as np
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
import re
import streamlit as st
import networkx as nx
import plotly.graph_objects as go
import time
from datetime import datetime, timedelta
import igraph
import pathpy as pp
from IPython.display import *
from IPython.display import HTML
from pathpy import Paths
from matplotlib.pyplot import *
import matplotlib.pyplot as plt
import plotly.express as px 
from itertools import combinations
from collections import defaultdict, deque
from pandas import Timestamp
from concurrent.futures import ThreadPoolExecutor
import requests
from bs4 import BeautifulSoup

c:\ProgramData\Anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


# NS API Request

In [1]:
# Define the endpoint and parameters
endpoint1 = "https://gateway.apiportal.ns.nl/Stationsplattegrond/Stations?returnGeometry={returnGeometry}&outSR={outSR}&returnCountOnly={returnCountOnly}&resultRecordCount={resultRecordCount}&resultOffset={resultOffset}"
params = {'extension': 'extension'}

# Define the headers
headers = {'Cache-Control': 'no-cache', 'Ocp-Apim-Subscription-Key': '7c2f112b78844f8a954dd6757d78831d', }

# Send the GET request
response = requests.get(endpoint1, params=params, headers=headers)
print("Status code:", response.status_code)

print("Response content:", response.content)
# Check the status code and print the response
if response.status_code == 200:
    data = response.json()
    df_stations = pd.DataFrame(data)
    # print(data)
else:
    print(f"Error: {response.status_code}")

names_coordinates = []

# Loop over each feature in the data 
for i in range(len(df_stations['features'])):
    # Extract station name and coordinates of that station
    stations_name = data['features'][i]['properties']['StationsNaam']
    coordinates_station = data['features'][i]['geometry']['coordinates'][0:2]
    # Add to list   
    names_coordinates.append((stations_name, coordinates_station))
names_coordinates = [(i[0],i[1][::-1]) for i in names_coordinates]

Status code: 200
Response content: b'{"type":"FeatureCollection","features":[{"type":"Feature","geometry":{"type":"Point","coordinates":[6.0039990409392079,52.8805527761048]},"properties":{"StationsNaam":"Wolvega","StationsCode":"WV0000"}},{"type":"Feature","geometry":{"type":"Point","coordinates":[4.5317605573261046,52.37569784728808]},"properties":{"StationsNaam":"Zandvoort aan Zee","StationsCode":"ZVT000"}},{"type":"Feature","geometry":{"type":"Point","coordinates":[4.9369999357594656,52.323379667705147]},"properties":{"StationsNaam":"Duivendrecht","StationsCode":"DVD000"}},{"type":"Feature","geometry":{"type":"Point","coordinates":[5.0076985019768712,52.10285243738273]},"properties":{"StationsNaam":"Vleuten","StationsCode":"VTN000"}},{"type":"Feature","geometry":{"type":"Point","coordinates":[4.6554025042786922,52.478611209528175]},"properties":{"StationsNaam":"Beverwijk","StationsCode":"BV0000"}},{"type":"Feature","geometry":{"type":"Point","coordinates":[5.6982666453869255,51.248

In [2]:
names_coordinates = []

# Loop over each feature in the data 
for i in range(len(df_stations['features'])):
    # Extract station name and coordinates of that station
    stations_name = data['features'][i]['properties']['StationsNaam']
    coordinates_station = data['features'][i]['geometry']['coordinates'][0:2]
    # Add to list
    names_coordinates.append((stations_name, coordinates_station))
names_coordinates = [(i[0],i[1][::-1]) for i in names_coordinates]

# Webscraper Rijdendetreinen.nl

In [ ]:
URL = "https://www.rijdendetreinen.nl/en/disruptions/archive"
r = requests.get(URL)
print(r.content)

In [ ]:
# # Define dictionary to store scraped data    
wym = {'data_key': [], 
       'source': [],
       'info': [],
       'date': [], 
       'page': []}

# Loop through all the pages on rijdendetreinen.nl    
for page in range(1,2589):
    print(page)
    
    # Define the URL and obtain response
    URL = f"https://www.rijdendetreinen.nl/en/disruptions/archive?page={page}"
    r = requests.get(URL)

    # Make into a BeautifulSoup object
    soup = BeautifulSoup(r.content)#, 'html5lib') # If this line causes an error, run 'pip install html5lib' or install html5lib 

    # Find the div with the disruptions
    a= soup.find('div', attrs = {'id':'w5', 'class': 'list-view'})

    # Loop through all the items in the div and only append items with 'data-key' or a certain class to list
    lst=[]
    for item in a:
        if item == '\n': 
            pass
        elif item.has_attr('data-key'):
            lst.append(item)
        elif ' '.join(item['class']) == 'font-bold text-l pt-6':
            lst.append(item)

    # Loop through all the items and find and append to the dictionary
    for j in lst:
        if j.has_attr('data-key'):
            wym['data_key'].append(j['data-key'])
            wym['source'].append(j.find('a')['href'])
            wym['info'].append(j.find('a').text)
            wym['date'].append(date)
            wym['page'].append(page)
        
        elif j.has_attr('class'):
            if ' '.join(j['class']) == 'font-bold text-l pt-6':
                date = j.text
        else:
            print('error')

    time.sleep(float(random.randrange(0,200)/100))

pd.DataFrame(wym).to_csv('disruptions.csv', index=False)
df = pd.read_csv("\Data\disruptions.csv") 
df

# Data Preprocessing

In [17]:
# Open CSV as df
df=pd.read_csv("\Data\disruptions.csv")

# Split 'info' column into new columns 'stations', 'reason', 'start_time', 'end_time', 'total_time'
df["stations"]=[df["info"][i].split("\n")[5] for i in range(len(df))]
df["reason"]=[df["info"][i].split("\n")[7] for i in range(len(df))]
df["start_time"]=[df["info"][i].split("\n")[9] for i in range(len(df))]
df["end_time"]=[df["info"][i].split("\n")[10] for i in range(len(df))]
df["total_time"]=[df["info"][i].split("\n")[11] for i in range(len(df))]
# Convert the 'date' column to datetime
df['date'] = pd.to_datetime(df['date'])     

# Drop the 'info' column
df.drop(index=[0,1,3,5],inplace=True)   # Drop the first 5 rows as they are not disruptions
df.reset_index(inplace=True,drop=True)  # Reset the index
df.head(1)  

# Replace • in 'end_time'   
df['end_time'] = df['end_time'].str.replace('•', '')

# Replace - in 'start_time'
df['start_time'] = df['start_time'].str.replace('-', '')

def get_stations(strng):
    # Regular expression pattern to match the desired part

    # Find the matched part
    match = re.search(r'([A-Z][a-zA-Z\s-]+-[A-Z][a-zA-Z\s-]+)', strng)

    if match:
        desired_part = match.group(1)
        return desired_part
    else:
        return np.nan
    
c=0
for i in range(len(df)):
    if re.search(r"\d", df.loc[i,"stations"]):
        c+=1
        df.loc[i,"stations"]=get_stations(df.loc[i,"stations"])
    if not pd.isna(df.loc[i,"stations"]):
        for word in [" en ","geen rechtstreekse","aanvulling","grote drukte","informatie","sprinters","let op:","spitspendels","meer info","ochtendspits","nachtnet","materieelinzet","treinen","treinverkeer","dienstregeling","storing","spoedreparatie","werkzaamheden","herstelwerkzaamheden","ontmanteling","morgen minder"]: #" en ", -> 555-537 keer dit ipv station1-station2, maar dit zou je kunnen vervangen door een '-' waardoor bovenstaande de code hierboven hem misschien kan vinden?? 
            if word in df.loc[i,"stations"].lower():
                c+=1
                df.loc[i,"stations"]=np.nan
                break


traject_lst=[]
hsl_lst=[]
for i in range(len(df)):

    s = df.loc[i,"stations"]
    if pd.isna(s):  
        traject_lst.append([])
        hsl_lst.append(np.nan)  
        continue
    temp_lst=[]  

    # Check if 'HSL' is there --> if yes then set to 1, otherwise 0
    if "HSL" in s:
        hsl_lst.append(1)
    else:
        hsl_lst.append(0)

    # Check if it is ..-../../.. format or ..-..-.. or ..-.. ; ..-..


    if "'s-Hertogenbosch" in s:
        s=s.replace("'s-Hertogenbosch","'s Hertogenbosch")    # Remove - from 's-Hertogenbosch
    if "Alphen a/d Rijn" in s:
        s=s.replace("Alphen a/d Rijn","Alphen aan den Rijn")       # Remove / from Alphen a/d Rijn
    if "Ede-Wageningen" in s:
        s=s.replace("Ede-Wageningen","Ede Wageningen")        # Remove - from Ede-Wageningen
    if "Liège / Luik" in s:
        s=s.replace("Liège / Luik","Luik")                    # Replace Liège / Luik with Luik
    if "Antwerpen-C." in s:
        s=s.replace("Antwerpen-C.","Antwerpen Centraal")            # Remove - from Antwerpen-C.
    if "Antwerpen-Centr" in s:
        s=s.replace("Antwerpen-Centr","Antwerpen Centraal")
    if "Etten-Leur" in s:
        s=s.replace("Etten-Leur","Etten Leur")
    if "Gilze-Rijen" in s:
        s=s.replace("Gilze-Rijen","Gilze Rijen")
    if "Eindhoven Strijp-S" in s:
        s=s.replace("Eindhoven Strijp-S","Eindhoven Strijp S")
    

    # Make list of stations where each traject is , seperated if excisting 
    if ";" in s:
        s = s.split("; ")
        # check stations
        for t in s:
            t = t.split("-")
            temp_lst.extend([t[i]+"-"+t[i+1] for i in range(len(t)) if i+1<len(t)])

    elif "," in s:
        s = s.split(", ")
        # check stations
        for t in s:
            t = t.split("-")
            temp_lst.extend([t[i]+"-"+t[i+1] for i in range(len(t)) if i+1<len(t)])

    elif "/" not in s:
        s = s.split("-")
        temp_lst.extend([s[i]+"-"+s[i+1] for i in range(len(s)) if i+1<len(s)])

    elif "/" in s:
        s=s.split("-")
        s1 = s[0]
        try:
            temp_lst.extend([s1+"-"+t for t in s[1].split("/")])
        except:
            temp_lst=[]

    # Add all lists to tracject_lst
    traject_lst.append(temp_lst)

# for i,j in enumerate(traject_lst):
#     print(i,j,hsl_lst[i])

df["trajecten"]=traject_lst
df["HSL"]=hsl_lst


# ---------------------------------------------------------------------------------------------------------------------------------------------------------

# Drop 15-04-2024 as the end times of the disruptions are not known yet 
df = df[df['date'] != '2024-04-15'].reset_index(drop=True).copy()
# Start from 2017 
#df['date'] = pd.to_datetime(df['date'])
df = df[df['date'].dt.year >= 2017]
# Since April 1st, station 'Hoek van Holland' is no longer considered a station by the NS.
# Since April 1st, station 'Maassluis' is no longer considered a station by the NS.
# ---------------------------------------------------------------------------------------------------------------------------------------------------------

dct_stations={"begin_station":[],
              "eind_station":[]
             }

row_stations=[]


for i in range(len(df)):
    if len(df.loc[i,"trajecten"])==1:
        steden=df.loc[i,"trajecten"][0].split("-")
        dct_stations["begin_station"].append(steden[0])
        dct_stations["eind_station"].append(steden[1])

    elif len(df.loc[i,"trajecten"])>1:
        steden=df.loc[i,"trajecten"][0].split("-")
        dct_stations["begin_station"].append(steden[0])
        dct_stations["eind_station"].append(steden[1])

        trjctn = df.loc[i,"trajecten"]

        for j in range(1,len(trjctn)):
            steden=trjctn[j].split("-")
            temp_lst = list(df.loc[i]) + [steden[0],steden[1]]
        row_stations.append(temp_lst)

    else:
        dct_stations["begin_station"].append(np.nan)
        dct_stations["eind_station"].append(np.nan)

# add columns to existing df
df["begin_station"] = dct_stations["begin_station"]
df["eind_station"] = dct_stations["eind_station"]

# Convert each list into a DataFrame
new_rows_df = pd.DataFrame(row_stations, columns=df.columns)

# Append the new rows DataFrame to the existing DataFrame
df = pd.concat([df,new_rows_df], ignore_index=True).copy()

# Remove whitespaces from 'begin_station' and 'eind_station'
df['begin_station'] = df['begin_station'].str.strip()
df['eind_station'] = df['eind_station'].str.strip()

df.sort_values('data_key').head(2)

# ---------------------------------------------------------------------------------------------------------------------------------------------------------
# Replace stations in 'begin_station' and 'end_station' by correct name of names_coordinates

# Overview of exceptions being matched to multiple values in names_coordinates, and their correct match
exceptions = {'Rotterdam': 'Rotterdam Centraal',
 'Amsterdam': 'Amsterdam Centraal',
 'Den Haag': 'Den Haag Centraal',
 'Utrecht': 'Utrecht Centraal',
 'Dordrecht': 'Dordrecht',
 'Eindhoven': 'Eindhoven Centraal',
 'Amersfoort': 'Amersfoort Centraal',
 "'s Hertogenbosch": "'s-Hertogenbosch",
 'Hengelo': 'Hengelo',
 'Tilburg': 'Tilburg',
 'Alkmaar': 'Alkmaar',
 'Apeldoorn': 'Apeldoorn',
 'Deventer': 'Deventer',
 'Schiphol': 'Schiphol Airport',
 'Leeuwarden': 'Leeuwarden',
 'Hilversum': 'Hilversum',
 'Groningen': 'Groningen',
 'Ede Wageningen': 'Ede-Wageningen',
 'Lelystad': 'Lelystad Centrum',
 'Maastricht': 'Maastricht',
 'Enschede': 'Enschede',
 'Driebergen': 'Driebergen-Zeist',
 'Naarden': 'Naarden-Bussum',
 'Hardinxveld': 'Boven Hardinxveld',
 'Eindhoven Strijp': 'Eindhoven Strijp-S',
 'Zwanenburg': 'Halfweg-Zwanenburg',
 'Nijmegen': 'Nijmegen',
 'Vlissingen': 'Vlissingen',
 'Winterswijk': 'Winterswijk',
 'Doetinchem': 'Doetinchem',
 'Delfzijl': 'Delfzijl',
 'Den Helder': 'Den Helder',
 'Barneveld': 'Barneveld Centrum',
 'Veenendaal': 'Veenendaal Centrum',
 'Kerkrade': 'Kerkrade Centrum',
 'Zandvoort': 'Zandvoort aan Zee',
 'Prinsenbeek': 'Breda Prinsenbeek',
 'Lutterade': 'Geleen-Lutterade',
 'Den Haag C': 'Den Haag Centraal',
 'Giessendam': 'Hardinxveld-Giessendam',
 'Sevenum': 'Horst-Sevenum',
 'Biezelinge': 'Kapelle-Biezelinge'}

# Overview of exceptions that are not in names_coordinates 
more_exceptions={'Aachen':"Aachen Hbf",
 'Almere':"Almere Centrum",
 'Antwerpen':"Antwerpen-Centraal",
 'Arnhem':"Arnhem Centraal",
 'Basel SBB':"Basel SBB",
 'Berlin':"Berlin Hbf",
 'Bielefeld':"Bielefeld Hbf",
 'Breda (HSL)':"Breda",
 'Brussel':"Brussel-Centraal",
 'Brussel (HSL)':"Brussel-Centraal",
 'Bussum':"Naarden-Bussum",
 'Dortmund':"Dortmund Hbf",
 'Duisburg':"Duisburf Hbf",
 'Düsseldorf':"Düsseldorf",
 'Eindhoven (HSL)':"Eindhoven Centraal",
 'Eindhoven Strijp S': "Eindhoven Strijp-S",
 'Essen (B)':"Essen",
 'Etten Leur':"Etten-Leur",
 'Frankfurt':"Frankfurt (M) Hbf",
 'Geleen':"Geleen-Lutterade",
 'Gilze Rijen':"Gilze-Rijen",
 'Gronau':"Gronau (Westf.)",
 'Halfweg':"Halfweg-Zwanenburg",
 'Hannover':"Hannover Hbf",
 'Hasselt':"Hasselt",
 'Herzogenrath':"Herzogenrath",
 'Hoek van Holland':"Hoek van Holland",
 'Horst':"Horst-Sevenum",
 'Kapelle':"Kapelle-Biezelinge",
 'Köln':"Koln",
 'Leer':"Leer (Ostfriesl)",
 'Leiden':"Leiden Centraal",
 'London (HSL)':"London St. Pancras Int.",
 'Luik':"Luik",
 'Maassluis':"Maassluis",
 'Mönchengladbach':"Monchengladbach",
 'Münster':"Munster (Westf.)",
 'Nord':"Nordwalde",
 'Paris':"Paris-Nord",
 'Paris (HSL)':"Paris-Nord",
 'Puurs':"Puurs",
 'Randwijck':"Maastricht Randwyck",
 'Rotterdam (HSL)':"Rotterdam Centraal",
 'Schiphol (HSL)':"Schiphol Airport",
 'Spoorwegmuseum':"Spoorwegmuseum",
 'Zeist':"Driebergen-Zeist"
}

def find_similar_values(column, names_coordinates, exceptions, threshold=90):
    updated_values = {}
    unique_values = column.dropna().unique()  # Drop NaN values before processing
    for value in unique_values:
        if value in exceptions:  # Check if the value has an exception
            updated_values[value] = exceptions[value]  # Add the exception to the updated values dictionary
        else:
            matches = process.extract(value, names_coordinates, limit=len(names_coordinates))
            relevant_matches = [m for m in matches if m[1]>=threshold]
            for match in relevant_matches:
                #print(value,match)
                if match[0][0] != value and match[1] >= threshold:
                    updated_values[value] = (match[0], names_coordinates[match[2]][1])
                    break  # Break after finding the first match
    df[column.name].replace(updated_values, inplace=True)
    
    return updated_values

# Usage
updated_values_begin = find_similar_values(df['begin_station'], names_coordinates, exceptions, threshold=90)
updated_values_end = find_similar_values(df['eind_station'], names_coordinates, exceptions, threshold=90)


df['begin_station'].replace(more_exceptions, inplace=True)
df['eind_station'].replace(more_exceptions, inplace=True)

# ---------------------------------------------------------------------------------------------------------------------------------------------------------
# Add new columns with coordinates of station names 

# Dict of stattion names in df that are not in names_coordinates and its coordinates
# Retrieved by Google search 
manual_coordinates = {
    'Brussel-Centraal': [50.8455, 4.3571],
    'Antwerpen-Centraal': [51.2169, 4.4212],
    'Koln' : [50.9432, 6.9586],
    'Hannover Hbf': [52.3765, 9.7410],
    'Duisburf Hbf' : [51.4297, 6.7769],
    'Paris-Nord' : [48.8805, 2.3550],
    'Monchengladbach' : [51.1995, 6.4731],
    'Gronau (Westf.)' : [52.2151, 7.0219], 
    'London St. Pancras Int.': [51.5311, 0.1259],
    'Düsseldorf': [51.2201, 6.7927],
    'Luik': [50.6244, 5.5667],
    'Herzogenrath': [50.8709, 6.0947],
    'Hoek van Holland': [51.9868, 4.1063],
    'Frankfurt (M) Hbf': [50.1071, 8.6638],
    'Berlin Hbf': [52.5251, 13.3694],
    'Essen': [51.4400, 7.0230],
    'Maassluis': [51.9174, 4.2530], 
    'Aachen Hbf': [50.7682, 6.0908],
    'Nordwalde': [52.077618, 7.461706],
    'Spoorwegmuseum': [52.0880, 5.1312],
    'Basel SBB': [47.5475, 7.5896],
    'Dortmund Hbf': [51.5172, 7.4592],
    'Duisburf Hbf': [51.4297, 6.7769],
    'Munster (Westf.)': [51.9569, 7.6349],
    'Hasselt': [50.9308, 5.3280],
    'Bielefeld Hbf': [52.0293, 8.5332],
    'Leer (Ostfriesl)': [53.23165, 7.465283],
    'Puurs': [51.0769, 4.2835]
}

# Combine initial and new coordinates into a single dictionary for lookup
combined_coordinates = {name: coords for name, coords in names_coordinates}
combined_coordinates.update(manual_coordinates)

# Function to get coordinates from the combined dictionary or track unmatched stations
def get_combined_coordinates(station_name):
    if station_name in combined_coordinates:
        return combined_coordinates[station_name]
    else:
        return None

# Add new columns for coordinates using the combined dictionary
df['begin_coordinates'] = df['begin_station'].apply(lambda x: get_combined_coordinates(x))
df['eind_coordinates'] = df['eind_station'].apply(lambda x: get_combined_coordinates(x))

# ---------------------------------------------------------------------------------------------------------------------------------------------------------
# Drop columns that are irrelevant for definining nodes, edges, attributes, and timestamps
df = df.dropna(subset=['begin_coordinates', 'eind_coordinates']).reset_index(drop=True)
df = df.drop(columns=['source', 'info', 'page', 'stations'])
df.to_pickle("disruptions.pkl")

2024-06-13 14:05:16.846 INFO    numexpr.utils: Note: NumExpr detected 12 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2024-06-13 14:05:16.846 INFO    numexpr.utils: NumExpr defaulting to 8 threads.


# Summary Stats

In [9]:
df[df['total_time']=='0 seconds']

data_key       date                        reason start_time  \
66        52926 2024-04-09               stranded train    3:59 PM    
251       52731 2024-03-28            broken down train    7:45 AM    
271       52709 2024-03-27      defective railway track    1:21 PM    
380       52597 2024-03-20               points failure    6:31 AM    
436       52535 2024-03-16            broken down train    9:07 PM    
...         ...        ...                           ...        ...   
43347     17221 2017-04-19  person on the railway track    4:32 PM    
43353     17208 2017-04-18            broken down train    4:12 PM    
43511     16529 2017-02-16            broken down train    7:12 AM    
43530     16471 2017-02-09            cause yet unknown   11:40 PM    
43557     16381 2017-02-01        an earlier disruption    9:43 PM    

        end_time total_time  \
66      3:59 PM   0 seconds   
251     7:46 AM   0 seconds   
271     1:22 PM   0 seconds   
380     6:31 AM   0 seconds   
436     9:08 PM   0 seconds   
...          ...        ...   
43347   4:32 PM   0 seconds   
43353   4:12 PM   0 seconds   
43511   7:12 AM   0 seconds   
43530  11:40 PM   0 seconds   
43557   9:43 PM   0 seconds   

                                               trajecten  HSL  \
66                           [Schiphol-Rotterdam (HSL) ]  1.0   
251                                 [Hengelo-Oldenzaal ]  0.0   
271           [Groningen-Delfzijl, Groningen-Eemshaven ]  0.0   
380    [Leiden-Den Haag, Amsterdam-Schiphol, Schiphol...  1.0   
436                                 [Amsterdam-Utrecht ]  0.0   
...                                                  ...  ...   
43347                  [Utrecht-Arnhem, Utrecht-Rhenen ]  0.0   
43353           [Dordrecht-Breda, Dordrecht-Roosendaal ]  0.0   
43511            [Leiden-Rotterdam, Den Haag-Rotterdam ]  0.0   
43530  [Den Haag-Rotterdam, Rotterdam-Eindhoven (HSL)...  1.0   
43557  [Eindhoven-Weert, Eindhoven-Roermond, Eindhove...  0.0   

              begin_station        eind_station  \
66         Schiphol Airport  Rotterdam Centraal   
251                 Hengelo           Oldenzaal   
271               Groningen            Delfzijl   
380         Leiden Centraal   Den Haag Centraal   
436      Amsterdam Centraal    Utrecht Centraal   
...                     ...                 ...   
43347      Utrecht Centraal              Rhenen   
43353             Dordrecht          Roosendaal   
43511     Den Haag Centraal  Rotterdam Centraal   
43530  Tilburg Universiteit  Eindhoven Centraal   
43557    Eindhoven Centraal             Heerlen   

                             begin_coordinates  \
66      [52.30896977401392, 4.761761478620183]   
251     [52.26145176012177, 6.794657502512164]   
271      [53.21101143709807, 6.56503443477492]   
380    [52.16634944827536, 4.4828157115070875]   
436       [52.3790023781832, 4.89971923396636]   
...                                        ...   
43347   [52.08948571864036, 5.109500171204091]   
43353   [51.80728472963318, 4.668515308446002]   
43511   [52.08045910491572, 4.324819198699884]   
43530  [51.565088748533185, 5.052609682698421]   
43557   [51.44293527679904, 5.480640426569133]   

                              eind_coordinates  
66      [51.92467496198316, 4.468742715036004]  
251     [52.30677497088962, 6.934189937277857]  
271    [53.33362586337313, 6.9239608763246645]  
380     [52.08045910491572, 4.324819198699884]  
436     [52.08948571864036, 5.109500171204091]  
...                                        ...  
43347  [51.95722148282205, 5.5781338690730555]  
43353   [51.54001133562578, 4.458700430244225]  
43511   [51.92467496198316, 4.468742715036004]  
43530   [51.44293527679904, 5.480640426569133]  
43557   [50.89102320845261, 5.974922512177946]  

[979 rows x 12 columns]

In [44]:
# Compute summary statistics
summary_stats = df.describe(include='all')

# Calculate frequency of most common values for categorical columns
freq_stats = {}
for column in df.columns:
    if df[column].dtype == 'object':
        most_common = df[column].value_counts().idxmax()
        freq_stats[column] = (most_common, df[column].value_counts().max())
    else:
        freq_stats[column] = (None, None)

# Print summary statistics
print("Summary Statistics")
print(summary_stats)

# Print most common value and frequency for categorical columns
print("\nMost Common Values and Frequencies")
for col, (val, freq) in freq_stats.items():
    if val is not None:
        print(f"{col}: Most common value = {val}, Frequency = {freq}")


Summary Statistics
            data_key        date              reason start_time  end_time  \
count   43674.000000       43674               43674      43674     43674   
unique           NaN        2656                  92       1414      1404   
top              NaN  2019-04-25  broken down train    4:38 PM   9:59 AM    
freq             NaN          77               15402         75       133   
mean    34505.781128         NaN                 NaN        NaN       NaN   
std     10743.125066         NaN                 NaN        NaN       NaN   
min     15950.000000         NaN                 NaN        NaN       NaN   
25%     25252.250000         NaN                 NaN        NaN       NaN   
50%     34422.500000         NaN                 NaN        NaN       NaN   
75%     43877.750000         NaN                 NaN        NaN       NaN   
max     52996.000000         NaN                 NaN        NaN       NaN   

       total_time                                       

# Temporal Network

In [13]:
# Load and preprocess data
df = pd.DataFrame(pd.read_pickle("Data\disruptions.pkl"))
# data = data.iloc[:1000].dropna().reset_index(drop=True).copy()
df["begin_coordinates"] = [[i[1], i[0]] for i in df["begin_coordinates"]]
df["eind_coordinates"] = [[i[1], i[0]] for i in df["eind_coordinates"]]

df['date'] = [d.date() for d in pd.to_datetime(df['date'])]


G = nx.MultiDiGraph()
    
# Add nodes and edges
for index, row in df.iterrows():
    if not G.has_node(row['begin_station']):
        G.add_node(row['begin_station'], pos=row['begin_coordinates'], station_name=row['begin_station'])
    if not G.has_node(row['eind_station']):
        G.add_node(row['eind_station'], pos=row['eind_coordinates'], station_name=row['eind_station'])

for index, row in df.iterrows():
    G.add_edge(row['begin_station'], row['eind_station'], reason=row['reason'], date=row['date'])

print(len(G.nodes))
print(len(G.edges))

126
43674


In [42]:
# 1. Number of nodes
num_nodes = G.number_of_nodes()

# 2. Number of time-stamped links
num_edges = G.number_of_edges()

# 3. Links/Nodes ratio
links_per_node = num_edges / num_nodes if num_nodes != 0 else 0

# 4. Observation period
# Assuming edges have 'date' as an attribute
dates = [edge_data['date'] for u, v, edge_data in G.edges(data=True)]
min_date = min(dates)
max_date = max(dates)
observation_period = (min_date.toordinal(), max_date.toordinal())  # Converting to ordinal for numeric range

# 5. Observation length
observation_length = (max_date - min_date).days  # Number of days between min and max date

# 6. Unique time stamps
unique_time_stamps = len(set(dates))

# 7. Average inter-event time (dt)
sorted_dates = sorted(set(dates))
inter_event_times = np.diff([d.toordinal() for d in sorted_dates])  # Time differences in days
avg_inter_event_dt = np.mean(inter_event_times) if len(inter_event_times) > 0 else 0

# 8. Min/Max inter-event dt
min_inter_event_dt = np.min(inter_event_times) if len(inter_event_times) > 0 else 0
max_inter_event_dt = np.max(inter_event_times) if len(inter_event_times) > 0 else 0

# Print the results
print(f"Attribute Value")
print(f"Nodes: {num_nodes}")
print(f"Time-stamped links: {num_edges}")
print(f"Links/Nodes: {links_per_node:.2f}")
print(f"Observation period: {observation_period}")
print(f"Observation length: {observation_length} days")
print(f"Unique time stamps: {unique_time_stamps}")
print(f"Avg. inter-event dt: {avg_inter_event_dt:.2f} days")
print(f"Min/Max inter-event dt: {min_inter_event_dt} / {max_inter_event_dt} days")


Attribute Value
Nodes: 126
Time-stamped links: 43674
Links/Nodes: 346.62
Observation period: (736330, 738990)
Observation length: 2660 days
Unique time stamps: 2656
Avg. inter-event dt: 1.00 days
Min/Max inter-event dt: 1 / 2 days


In [73]:
# Ensure 'date' is in datetime format
df['date'] = pd.to_datetime(df['date'])

# Group by 'date' and count disruptions per day
disruptions_per_day = df.groupby(df['date'].dt.date).size()

# Calculate the average number of disruptions per day
average_disruptions_per_day = disruptions_per_day.mean()

# Print the results
print(f"Average number of disruptions per day: {average_disruptions_per_day:.2f}")

Average number of disruptions per day: 16.44


# Metrics

In [44]:
df = pd.read_pickle("Data\disruptions.pkl")

In [57]:
# Select only part of dataset due to computational limitations
# Convert the date column to datetime format if it's not already
df['date'] = pd.to_datetime(df['date'])

# Filter the DataFrame for Jan, Feb, and March 2024
filtered_df = df[df['date'].dt.year.isin([2024]) & df['date'].dt.month.isin([1,2,3])]

G = nx.MultiDiGraph()
    
# Add nodes and edges
for index, row in filtered_df.iterrows():
    if not G.has_node(row['begin_station']):
        G.add_node(row['begin_station'], pos=row['begin_coordinates'], station_name=row['begin_station'])
    if not G.has_node(row['eind_station']):
        G.add_node(row['eind_station'], pos=row['eind_coordinates'], station_name=row['eind_station'])

for index, row in filtered_df.iterrows():
    G.add_edge(row['begin_station'], row['eind_station'], reason=row['reason'], date=row['date'])

print(len(G.nodes))
print(len(G.edges))

106
1759


## Temporal Degree

In [58]:
def temporal_degree(G):
    temporal_degree_dict = defaultdict(int)
    for u, v, data in G.edges(data=True):
        temporal_degree_dict[u] += 1
        if not G.is_directed():
            temporal_degree_dict[v] += 1
    return temporal_degree_dict

defaultdict(int,
            {'Arnhem Centraal': 50,
             'Zutphen': 13,
             'Zwolle': 93,
             'Deventer': 21,
             'Schiphol Airport': 137,
             'Rotterdam Centraal': 117,
             'Dordrecht': 77,
             'Breda': 52,
             'Utrecht Centraal': 227,
             'Groningen': 42,
             'Haarlem': 28,
             'Alkmaar': 23,
             'Hengelo': 20,
             'Amersfoort Centraal': 52,
             'Ede-Wageningen': 7,
             'Heerlen': 53,
             "'s-Hertogenbosch": 34,
             'Amsterdam Centraal': 222,
             'Gouda': 6,
             'Leeuwarden': 9,
             'Eindhoven Centraal': 40,
             'Roosendaal': 47,
             'Leiden Centraal': 49,
             'Enschede': 1,
             'Almelo': 10,
             'Alphen aan den Rijn': 9,
             'Den Haag Centraal': 37,
             'Antwerpen-Centraal': 11,
             'Venlo': 25,
             'Monchengladbach': 14,
    

In [68]:
degree_dict = temporal_degree(G)

# Get top 10 highest values
top_10 = sorted(degree_dict.items(), key=lambda item: item[1], reverse=True)[:10]

# Average temporal degree
average_degree = sum(degree_dict.values()) / len(degree_dict)

# Output the results
print("Top 10 nodes with the highest temporal degrees:")
for node, degree in top_10:
    print(f"Node: {node}, Temporal Degree: {degree}")

print(f"Average Temporal Degree: {average_degree}")

Top 10 nodes with the highest temporal degrees:
Node: Utrecht Centraal, Temporal Degree: 227
Node: Amsterdam Centraal, Temporal Degree: 222
Node: Schiphol Airport, Temporal Degree: 137
Node: Rotterdam Centraal, Temporal Degree: 117
Node: Zwolle, Temporal Degree: 93
Node: Dordrecht, Temporal Degree: 77
Node: Heerlen, Temporal Degree: 53
Node: Breda, Temporal Degree: 52
Node: Amersfoort Centraal, Temporal Degree: 52
Node: Arnhem Centraal, Temporal Degree: 50
Average Temporal Degree: 33.18867924528302


## Temporal Betweenness and Shortest Paths

In [59]:
def find_temporal_shortest_paths(G, source, target, time_attr): 
    shortest_paths = []
    min_length = float('inf')
    queue = deque([(source, [source], -float('inf'))])
    visited = set()
    
    while queue:
        current, path, last_time = queue.popleft()
        
        if current == target:
            if len(path) < min_length:
                shortest_paths = [path]
                min_length = len(path)
            elif len(path) == min_length:
                shortest_paths.append(path)
            continue
        
        if (current, last_time) in visited:
            continue
        visited.add((current, last_time))
        
        neighbors = G.successors(current) if G.is_directed() else G.neighbors(current)
        
        for neighbor in neighbors:
            for key, edge_data in G[current][neighbor].items():
                edge_time = edge_data[time_attr]
                if isinstance(edge_time, datetime):
                    edge_time = edge_time.timestamp()  # Convert Timestamp to seconds
                if edge_time > last_time:
                    queue.append((neighbor, path + [neighbor], edge_time))
    
    return shortest_paths

In [69]:
node_names = filtered_df['begin_station'].unique()
end_node_names = filtered_df['eind_station'].unique()

for node_name in node_names:
    for node_name2 in end_node_names:
        if node_name != node_name2:
            print(f"Shortest paths from {node_name} to {node_name2}:")
            paths = find_temporal_shortest_paths(G, node_name, node_name2, 'date')
            print(paths)

Shortest paths from Arnhem Centraal to Zutphen:
[['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen'], ['Arnhem Centraal', 'Zutphen']]
Shortest paths from Arnhem Centraal to Doetinchem:
[['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem'], ['Arnhem Centraal', 'Doetinchem']]
Shortest paths from Arnhem Centraal to Deventer:
[]
Shortest paths from Arnhem Centraal to Rotterdam Centraal:
[]
Shortest paths from Arnhem Centraal to Breda:
[]
Shortest paths from Ar

In [70]:
def temporal_betweenness(G, time_attr='time'):
    nodes = list(G.nodes())
    N = len(nodes)
    betweenness = {node: 0 for node in nodes}
    
    def process_pair(s, t):
        if s == t:
            return
        
        paths = find_temporal_shortest_paths(G, s, t, time_attr)
        if not paths:
            return
        
        sigma_st = len(paths)
        path_count = defaultdict(int)
        
        for path in paths:
            for i in range(1, len(path) - 1):
                path_count[path[i]] += 1
        
        for node in path_count:
            betweenness[node] += path_count[node] / sigma_st
    
    with ThreadPoolExecutor() as executor:
        for s in nodes:
            for t in nodes:
                executor.submit(process_pair, s, t)
    
    scale = 1 / ((N - 1) * (N - 2))
    for node in betweenness:
        betweenness[node] *= scale
    
    return betweenness

{'Arnhem Centraal': 0.012339926897928708,
 'Zutphen': 0.003550092555523494,
 'Doetinchem': 0.0,
 'Zwolle': 0.0243786063600194,
 'Deventer': 0.002695430229544799,
 'Schiphol Airport': 0.015528870515618071,
 'Rotterdam Centraal': 0.022206669841108386,
 'Dordrecht': 0.004404192857314361,
 'Breda': 0.01778484326921407,
 'Utrecht Centraal': 0.021463199440458262,
 'Groningen': 0.007326007326007326,
 'Haarlem': 0.0002222447104091095,
 'Alkmaar': 0.001098901098901099,
 'Hengelo': 0.004395604395604396,
 'Bielefeld Hbf': 0.0,
 'Amersfoort Centraal': 0.009637239255166831,
 'Ede-Wageningen': 0.003799350975821564,
 'Heerlen': 0.006569819069819069,
 'Aachen Hbf': 0.0,
 'Hoorn': 0.0,
 "'s-Hertogenbosch": 0.006582028101266565,
 'Amsterdam Centraal': 0.0,
 'Gouda': 0.0030758476759450157,
 'Leeuwarden': 0.0032967032967032967,
 'Enkhuizen': 0.0,
 'Eindhoven Centraal': 0.025284019928030758,
 'Roosendaal': 0.001540291083560314,
 'Vlissingen': 0.0,
 'Leiden Centraal': 0.016121401873750336,
 'Enschede': 0.00

In [71]:
# Compute betweenness
betweenness_dict = temporal_betweenness(G, time_attr='date')

# Get the top 10 highest values
top_10_betweenness = sorted(betweenness_dict.items(), key=lambda item: item[1], reverse=True)[:10]

# Calculate the average betweenness
average_betweenness = sum(betweenness_dict.values()) / len(betweenness_dict)

# Output the results
print("Top 10 nodes with the highest temporal betweenness:")
for node, betweenness in top_10_betweenness:
    print(f"Node: {node}, Betweenness: {betweenness}")

print(f"Average Temporal Betweenness: {average_betweenness}")

# Top 10 
top_10_betweenness_dict = dict(top_10_betweenness)

Top 10 nodes with the highest temporal betweenness:
Node: Eindhoven Centraal, Betweenness: 0.025284019928030765
Node: Zwolle, Betweenness: 0.0243786063600194
Node: Rotterdam Centraal, Betweenness: 0.022206669841108386
Node: Utrecht Centraal, Betweenness: 0.021463199440458262
Node: Breda, Betweenness: 0.01778484326921407
Node: Leiden Centraal, Betweenness: 0.016121401873750333
Node: Schiphol Airport, Betweenness: 0.015528870515618071
Node: Arnhem Centraal, Betweenness: 0.012339926897928708
Node: Lelystad Centrum, Betweenness: 0.010896144202649444
Node: Amersfoort Centraal, Betweenness: 0.009637239255166831
Average Temporal Betweenness: 0.0025450964130209414


## Temporal Closeness

In [67]:
def temporal_closeness(G, time_attr='time'):
    closeness = {}
    nodes = list(G.nodes())
    N = len(nodes)
    
    for s in nodes:
        distance = {node: float('inf') for node in nodes}
        distance[s] = 0
        Q = deque([(s, 0)])  # (node, current_time)
        
        while Q:
            current_node, current_time = Q.popleft()
            neighbors = G.successors(current_node) if G.is_directed() else G.neighbors(current_node)
            
            for neighbor in neighbors:
                for key in G[current_node][neighbor]:
                    edge_time = G[current_node][neighbor][key][time_attr]
                    if isinstance(edge_time, datetime):
                        edge_time = edge_time.timestamp()  # Convert Timestamp to seconds
                    if current_time <= edge_time < distance[neighbor]: 
                        distance[neighbor] = edge_time
                        Q.append((neighbor, edge_time))
        
        total_reciprocal_distance = sum([1/d for d in distance.values() if d != float('inf') and d != 0])
        reachable_nodes = len([d for d in distance.values() if d != float('inf') and d != 0])
        
        if reachable_nodes > 0:
            closeness[s] = total_reciprocal_distance / (N - 1)
        else:
            closeness[s] = 0
    
    return closeness

temporal_closeness(G, time_attr='date')

{'Arnhem Centraal': 1.6190046867324749e-10,
 'Zutphen': 2.7925944291425422e-11,
 'Doetinchem': 0,
 'Zwolle': 1.4507441074077883e-10,
 'Deventer': 5.5855009826301064e-11,
 'Schiphol Airport': 4.802023079785709e-10,
 'Rotterdam Centraal': 1.6753632027788002e-10,
 'Dordrecht': 1.3962014446770396e-10,
 'Breda': 1.2848115551817642e-10,
 'Utrecht Centraal': 4.4109323498201214e-10,
 'Groningen': 4.466485232303215e-11,
 'Haarlem': 3.459269522167559e-10,
 'Alkmaar': 1.1174623780920958e-11,
 'Hengelo': 1.6754719233474824e-11,
 'Bielefeld Hbf': 0,
 'Amersfoort Centraal': 2.7913009992918623e-10,
 'Ede-Wageningen': 1.673923706673914e-10,
 'Heerlen': 2.7927080312119972e-11,
 'Aachen Hbf': 0,
 'Hoorn': 0,
 "'s-Hertogenbosch": 8.937124604202925e-11,
 'Amsterdam Centraal': 5.360830652725343e-10,
 'Gouda': 1.6738014198370026e-10,
 'Leeuwarden': 1.1158517343184664e-11,
 'Enkhuizen': 0,
 'Eindhoven Centraal': 7.261934742178399e-11,
 'Roosendaal': 2.2307443049850026e-11,
 'Vlissingen': 0,
 'Leiden Centraal

In [72]:
# Compute temporal closeness
closeness_dict = temporal_closeness(G, time_attr='date')

# Get the top 10 highest values
top_10_closeness = sorted(closeness_dict.items(), key=lambda item: item[1], reverse=True)[:10]

# Calculate the average temporal closeness
average_closeness = sum(closeness_dict.values()) / len(closeness_dict)

# Output the results
print("Top 10 nodes with the highest temporal closeness:")
for node, closeness in top_10_closeness:
    print(f"Node: {node}, Closeness: {closeness:.12e}")

print(f"Average Temporal Closeness: {average_closeness:.12e}")

# Optionally store the top 10 in a dictionary for further processing
top_10_closeness_dict = dict(top_10_closeness)


Top 10 nodes with the highest temporal closeness:
Node: Amsterdam Centraal, Closeness: 5.360830652725e-10
Node: Amsterdam Sloterdijk, Closeness: 4.855526553356e-10
Node: Schiphol Airport, Closeness: 4.802023079786e-10
Node: Hoofddorp, Closeness: 4.745396025795e-10
Node: Utrecht Centraal, Closeness: 4.410932349820e-10
Node: Breukelen, Closeness: 4.354506304741e-10
Node: Haarlem, Closeness: 3.459269522168e-10
Node: Amsterdam Zuid, Closeness: 3.236051409176e-10
Node: Amsterdam Bijlmer ArenA, Closeness: 3.234733964779e-10
Node: Leiden Centraal, Closeness: 3.180185375120e-10
Average Temporal Closeness: 7.098305910059e-11


### Temporal Reachability

In [63]:
# Reachable Nodes: All nodes that can be visited starting from source respecting the temporal order of edges.

def find_reachable_nodes(G, source, time_attr):
    reachable = set()
    queue = deque([(source, -float('inf'))])
    visited = set()
    
    while queue:
        current, last_time = queue.popleft()
        
        if (current, last_time) in visited:
            continue
        visited.add((current, last_time))
        reachable.add(current)
        
        neighbors = G.successors(current) if G.is_directed() else G.neighbors(current)
        
        for neighbor in neighbors:
            for key, edge_data in G[current][neighbor].items():
                edge_time = edge_data[time_attr]
                if isinstance(edge_time, datetime):
                    edge_time = edge_time.timestamp()  # Convert Timestamp to seconds
                if edge_time > last_time:
                    queue.append((neighbor, edge_time))
    
    return reachable


In [64]:
for node_name in filtered_df['begin_station'].unique():
    x = find_reachable_nodes(G, node_name, time_attr='date')
    print(f"Reachable nodes from {node_name}: {x}")

Reachable nodes from Arnhem Centraal: {'Oldenzaal', 'Weert', 'Oss', 'Zutphen', 'Maastricht Randwyck', 'Düsseldorf', 'Roermond', 'Luik', 'Wijchen', 'Venray', 'Venlo', 'Arnhem Centraal', 'Tiel', 'Deurne', 'Tilburg', 'Sittard', 'Duisburf Hbf', 'Hengelo', 'Heerlen', 'Eindhoven Centraal', 'Aachen Hbf', "'s-Hertogenbosch", 'Enschede', 'Kerkrade Centrum', 'Monchengladbach', 'Maastricht', 'Bielefeld Hbf', 'Winterswijk', 'Doetinchem', 'Nijmegen'}
Reachable nodes from Zwolle: {'Oldenzaal', 'Bad Nieuweschans', 'Deventer', 'Zutphen', 'Stavoren', 'Harlingen Haven', 'Zwolle', 'Leer (Ostfriesl)', 'Arnhem Centraal', 'Leeuwarden', 'Groningen', 'Duisburf Hbf', 'Hengelo', 'Kampen', 'Delfzijl', 'Enschede', 'Almelo', 'Hardenberg', 'Bielefeld Hbf', 'Emmen', 'Eemshaven', 'Winterswijk', 'Doetinchem', 'Veendam', 'Gronau (Westf.)'}
Reachable nodes from Schiphol Airport: {'Vlissingen', 'Weert', 'Oss', 'Amersfoort Schothorst', 'Maastricht Randwyck', 'Dordrecht', 'Gouda', 'Zwolle', 'Leer (Ostfriesl)', 'Venlo', 'Si

In [65]:
# Reachability Ratio: The proportion of node pairs where one node can reach another respecting temporal constraints.

def calculate_reachability_ratio(G, time_attr):
    total_nodes = len(G.nodes)
    total_pairs = total_nodes * (total_nodes - 1)
    reachable_pairs = 0
    
    for node in G.nodes:
        reachable_nodes = find_reachable_nodes(G, node, time_attr)
        reachable_pairs += len(reachable_nodes) - 1  # Exclude the node itself
    
    reachability_ratio = reachable_pairs / total_pairs
    return reachability_ratio

calculate_reachability_ratio(G, time_attr='date')

0.11931716082659478

In [66]:
# Reachability Latency: The average shortest path length considering a fraction r of nodes at each time step, providing insight into the network’s temporal efficiency.

def reachability_latency(G, time_attr, r):
    T = len(set(data[time_attr] for u, v, data in G.edges(data=True)))
    N = len(G.nodes)
    
    d_t_i = np.zeros((T, N))
    
    for t, time in enumerate(sorted(set(data[time_attr] for u, v, data in G.edges(data=True)))):
        for i, node in enumerate(G.nodes):
            path_lengths = []
            for target in G.nodes:
                if node != target:
                    shortest_paths = find_temporal_shortest_paths(G, node, target, time_attr)
                    if shortest_paths:
                        path_lengths.append(len(shortest_paths[0]) - 1)
            if path_lengths:
                d_t_i[t, i] = np.mean(path_lengths)
    
    k = int(np.floor(r * N))
    
    R_r = (1 / (T * N)) * np.sum(np.sort(d_t_i, axis=1)[:, k])
    
    return R_r
reachability_latency(G, 'date', 0.1)


0.0

# ANIMATION

In [ ]:
# For this run Disruptions - Streamlit App.py

# Load and preprocess data
data = pd.DataFrame(pd.read_pickle("Data\disruptions.pkl"))
data = data.iloc[:1000].dropna().reset_index(drop=True).copy()
data["begin_coordinates"] = [[i[1], i[0]] for i in data["begin_coordinates"]]
data["eind_coordinates"] = [[i[1], i[0]] for i in data["eind_coordinates"]]

df = data.copy()
df['date'] = [d.date() for d in pd.to_datetime(df['date'])]

# Define a function to create the graph based on a selected date
def create_graph(selected_date):
    filtered_df = df[df['date'] == selected_date]
    G = nx.Graph()
    
    # Add nodes and edges
    for index, row in filtered_df.iterrows():
        G.add_node(row['begin_station'], pos=row['begin_coordinates'], station_name=row['begin_station'])
        G.add_node(row['eind_station'], pos=row['eind_coordinates'], station_name=row['eind_station'])
        G.add_edge(row['begin_station'], row['eind_station'], reason=row['reason'], date=row['date'])
    
    pos = nx.get_node_attributes(G, 'pos')
    edge_trace = []
    node_trace = []
    
    # Add edges first to ensure they are below nodes in the final plot
    for edge in G.edges(data=True):
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_trace.append(go.Scattermapbox(
            lon=[x0, x1, None],
            lat=[y0, y1, None],
            mode='lines',
            line=dict(width=2, color='blue'),
            text=edge[2]['reason'],
            hoverinfo='text',
            customdata=[edge[2]['reason']],
            name=f"{edge[0]} - {edge[1]}"
        ))
    
    # Add nodes
    for node in G.nodes():
        x, y = pos[node]
        node_trace.append(go.Scattermapbox(
            lon=[x],
            lat=[y],
            text=node,
            mode='markers',
            marker=dict(size=10),
            name=node,
            hoverinfo='text',
            customdata=[G.nodes[node]['station_name']]
        ))
    
    # Create the figure
    fig = go.Figure(data=edge_trace + node_trace)
    
    # Update layout for map display
    fig.update_layout(
        mapbox_style="open-street-map",
        width=500,
        height=500,
        margin=dict(l=5, r=5, b=5, t=5),
        mapbox=dict(
            center=go.layout.mapbox.Center(lat=52, lon=5.8),
            zoom=5.8,
        ),
        showlegend=False
    )
    
    # Adding interactivity
    for trace in fig.data:
        if trace.mode == 'markers':
            trace.hovertemplate = '<b>Station:</b> %{customdata}<extra></extra>'
        elif trace.mode == 'lines':
            trace.hovertemplate = '<b>Disruption Reason:</b> %{customdata}<extra></extra>'
    
    return fig

# set app title & Flavicon
st.set_page_config(page_title='NS Train Disruptions', layout='centered', page_icon="Disruptions - Streamlit NS Logo.png")


st.markdown("""
        <style>
               .block-container {
                    padding-top: 1rem;
                    padding-bottom: 0rem;
                }
        </style>
        """, unsafe_allow_html=True)


st.title("Train Disruptions Visualization")
key_nr=0

# Create placeholders for the slider and info display
slider_ph = st.empty()

# Initialize the datetime range and the initial value
unique_dates = df['date'].unique()
initial_value = min(unique_dates)
start_datetime = initial_value
end_datetime = max(unique_dates)

# Initialize session state variables for animation control
if 'animation' not in st.session_state:
    st.session_state.animation = False
if 'current_date' not in st.session_state:
    st.session_state.current_date = initial_value

# Create the slider and display the initial value
selected_date = slider_ph.slider("Select a Date", min_value=start_datetime, max_value=end_datetime, value=st.session_state.current_date, format="YYYY-MM-DD", key="initial_slider")

# Create graph for the selected date
fig = create_graph(selected_date)

# Display the graph
plot_ph = st.empty()
plot_ph.plotly_chart(fig, use_container_width=True)

# Animate button
animate_button_col, stop_button_col = st.columns([1, 1])  # Divide the available space into two columns
with animate_button_col:
    animate_button = st.button('Animate')

# Stop button
with stop_button_col:
    stop_button = st.button('Stop Animation')

# Handle the animate button click
if animate_button:
    st.session_state.animation = True

# Handle the stop button click
if stop_button:
    st.session_state.animation = False

# Animation loop
if st.session_state.animation:
    while st.session_state.animation:
        time.sleep(1)

        # Update the current date
        st.session_state.current_date += timedelta(days=1)

        # Reset the date if it exceeds the end date
        if st.session_state.current_date > end_datetime:
            st.session_state.current_date = initial_value

        # Update the slider and info display with a unique key
        selected_date = slider_ph.slider("Select a Date", min_value=start_datetime, max_value=end_datetime, value=st.session_state.current_date, format="YYYY-MM-DD", key=f"slider_{st.session_state.current_date}_{key_nr}")
        key_nr += 1

        # Update the graph
        fig = create_graph(st.session_state.current_date)
        plot_ph.plotly_chart(fig, use_container_width=True)


2024-05-27 16:42:47.272 
  command:

    streamlit run C:\Users\20213830\AppData\Roaming\Python\Python39\site-packages\ipykernel_launcher.py [ARGUMENTS]
2024-05-27 16:42:47.274 Session state does not function when running a script without `streamlit run`
